In [45]:
import numpy as np

class QRdecompose:
    '''Class to perform QR decomposition'''
    
    def __init__(self,A,tol=1.0e-10):
        self.A0=A
        self.N=A.shape[0]
        self.tol=tol
        
        [self.evals,self.evecs]=self.qr_steps()
        
        
    def qr_steps(self):
        '''Perform the QR steps until the off-diagonal elements are small enough'''
        V=np.identity(self.N)
        D=np.copy(self.A0)
        
        maxSteps=int(1e6) # In case we have trouble converging

        for step in range(maxSteps):

            Q,R=self.qr_decomp(D)
            
            D=np.matmul(R,Q)
            V=np.matmul(V,Q)
        
            diagD=np.diag(np.diagonal(D))
            maxOffDiag=np.amax(D-diagD)

            if (maxOffDiag < self.tol):
                return np.diagonal(D),V
        
        raise Exception('QR decomposition did not converge!')
        
        
        
    def qr_decomp(self,A):
        '''perform the QR decomposition'''
        
        Q=np.zeros((self.N,self.N))
        R=np.zeros((self.N,self.N))
        
        for ii in range(0,self.N):
            
            # Calculate u_i
            u=A[:,ii]
            for jj in range(0,ii):
                u-=np.matmul(Q[:,jj],A[:,ii])*Q[:,jj]

            if np.linalg.norm(u) < 1e-12:
                Q[:,ii] = 0
            else:
                Q[:,ii]=u/np.linalg.norm(u)
                
            # Now populate row of R
            R[ii,ii]=np.linalg.norm(u)
            if ii<self.N:
                R[ii,ii+1:]=np.matmul(Q[:,ii],A[:,ii+1:])
                
        return Q,R
            
    
        

In [46]:
# Simple example

A=np.array([[1,4,8,4],[4,2,3,7],[8,3,6,9],[4,7,9,2]],dtype='float')

eigA=QRdecompose(A)

np.set_printoptions(precision=4,suppress=True)
print(eigA.evals)
print()
print(eigA.evecs)
print()
print(np.transpose(eigA.evecs) @ A @ eigA.evecs)


[21. -8. -3.  1.]

[[ 0.4315 -0.3836 -0.7746 -0.2582]
 [ 0.3836  0.4315 -0.2582  0.7746]
 [ 0.6233  0.5274  0.2582 -0.5164]
 [ 0.5274 -0.6233  0.5164  0.2582]]

[[21.  0.  0. -0.]
 [ 0. -8.  0.  0.]
 [ 0.  0. -3. -0.]
 [-0.  0. -0.  1.]]


In [47]:
# Random (symmetric) matrix
nMatrix=10
A=np.random.rand(nMatrix,nMatrix)
A=A + A.T - np.diag(A.diagonal())
eigA=QRdecompose(A)

print(eigA.evals)
print(np.linalg.eigvalsh(A))

[10.1129 -2.4095 -1.844  -1.4394  1.0816 -0.9006  0.7167 -0.5894  0.2943
 -0.0944]
[-2.4095 -1.844  -1.4394 -0.9006 -0.5894 -0.0944  0.2943  0.7167  1.0816
 10.1129]


In [48]:
# Zero determinant matrix
A=np.array([[1,2,3],[2,4,6],[3,6,9]],dtype='float')

print('Determinant: ', np.linalg.det(A)) 

eigA=QRdecompose(A)

print(eigA.evals)
print(np.linalg.eigvals(A))


Determinant:  -1.1093356479670441e-31
[14.  0.  0.]
[14.  0. -0.]
